In [0]:
from pyspark.sql import SparkSession, Window
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, DoubleType
from pyspark.sql import functions as F
from pyspark.sql.functions import (
    col, lit, when, year, month, dayofmonth, hour, dayofweek, quarter,
    min, max, avg, stddev, variance, count, mean, to_date, date_format, 
    monotonically_increasing_id, isnan
)

Bronze Layer - Ingestion

In [0]:
# Define schema for Bronze Layer
bronze_schema = StructType([
    StructField("timestamp", StringType(), True),
    StructField("turbine_id", IntegerType(), True),
    StructField("wind_speed", DoubleType(), True),
    StructField("wind_direction", DoubleType(), True),
    StructField("power_output", DoubleType(), True)
])

# Step 1: Bronze Layer
bronze_df = (
    spark.read.format("csv")
    .option("header", "true")
    .schema(bronze_schema)
    .load("/FileStore/colibri/*.csv")
)

# Data Quality Checks

# 1. Check for duplicate rows
if bronze_df.count() != bronze_df.dropDuplicates().count():
    print("Soft warning: Duplicate rows found in Bronze Layer!")

# 2. Check for nulls in critical fields
critical_fields = ["timestamp", "turbine_id", "power_output"]
null_critical_fields = bronze_df.select(
    [col(f).isNull().alias(f"{f}_is_null") for f in critical_fields]
).filter(
    col(f"{critical_fields[0]}_is_null") |
    col(f"{critical_fields[1]}_is_null") |
    col(f"{critical_fields[2]}_is_null")
).count()

if null_critical_fields > 0:
    raise ValueError(f"Null values found in critical fields of Bronze Layer! ({null_critical_fields} rows)")

# 3. Check for invalid or null dates
invalid_dates = bronze_df.withColumn("date", to_date("timestamp")).filter(col("date").isNull()).count()
if invalid_dates > 0:
    print(f"Invalid or null timestamps found in {invalid_dates} rows!")

# 4. Check for unreasonable ranges in numerical fields
wind_speed_range = (0, 100)  # Example: 0 to 100 m/s
wind_direction_range = (0, 360)  # Example: 0 to 360 degrees
power_output_range = (0, 5000)  # Example: 0 to 5000 MW

out_of_range_count = bronze_df.filter(
    (col("wind_speed") < wind_speed_range[0]) | (col("wind_speed") > wind_speed_range[1]) |
    (col("wind_direction") < wind_direction_range[0]) | (col("wind_direction") > wind_direction_range[1]) |
    (col("power_output") < power_output_range[0]) | (col("power_output") > power_output_range[1])
).count()

if out_of_range_count > 0:
    print(f"Soft warning: Found {out_of_range_count} rows with out-of-range values in Bronze Layer!")

# 5. Check for non-numeric or NaN values in numerical fields
nan_count = bronze_df.select(
    [isnan(col(f)).alias(f"{f}_is_nan") for f in ["wind_speed", "wind_direction", "power_output"]]
).filter(
    col("wind_speed_is_nan") | col("wind_direction_is_nan") | col("power_output_is_nan")
).count()

if nan_count > 0:
    print(f"Soft warning: NaN values found in numerical fields ({nan_count} rows)!")

# Save Bronze Layer
bronze_df.write.format("delta").mode("overwrite").partitionBy("turbine_id").saveAsTable("bronze_turbine_data")
bronze_df.display()


timestamp turbine_id wind_speed wind_direction power_output 2022-03-01 00:00:00 11 9.1 269.0 2.9 2022-03-01 00:00:00 12 11.3 316.0 2.5 2022-03-01 00:00:00 13 11.2 148.0 3.7 2022-03-01 00:00:00 14 10.7 97.0 1.6 2022-03-01 00:00:00 15 11.0 81.0 4.4 2022-03-01 01:00:00 11 12.3 245.0 1.8 2022-03-01 01:00:00 12 11.0 293.0 2.2 2022-03-01 01:00:00 13 11.4 270.0 1.9 2022-03-01 01:00:00 14 10.4 140.0 2.3 2022-03-01 01:00:00 15 14.6 283.0 4.3 2022-03-01 02:00:00 11 14.3 135.0 2.9 2022-03-01 02:00:00 12 9.1 358.0 3.2 2022-03-01 02:00:00 13 13.7 67.0 3.1 2022-03-01 02:00:00 14 9.2 89.0 2.7 2022-03-01 02:00:00 15 9.7 303.0 4.5 2022-03-01 03:00:00 11 9.6 171.0 2.6 2022-03-01 03:00:00 12 11.0 175.0 2.4 2022-03-01 03:00:00 13 13.0 42.0 4.1 2022-03-01 03:00:00 14 13.6 198.0 3.1 2022-03-01 03:00:00 15 9.3 162.0 3.8 2022-03-01 04:00:00 11 9.2 316.0 4.2 2022-03-01 04:00:00 12 11.8 170.0 3.4 2022-03-01 04:00:00 13 14.3 333.0 2.3 2022-03-01 04:00:00 14 12.3 118.0 1.9 2022-03-01 04:00:00 15 9.6 213.0 4.0 2022-03-01 05:00:00 11 14.1 176.0 3.2 2022-03-01 05:00:00 12 12.9 15.0 1.6 2022-03-01 05:00:00 13 10.6 186.0 2.4 2022-03-01 05:00:00 14 12.6 207.0 1.7 2022-03-01 05:00:00 15 10.1 332.0 2.0 2022-03-01 06:00:00 11 14.5 251.0 3.5 2022-03-01 06:00:00 12 12.0 36.0 3.2 2022-03-01 06:00:00 13 9.4 270.0 3.2 2022-03-01 06:00:00 14 13.6 27.0 2.4 2022-03-01 06:00:00 15 14.0 124.0 3.7 2022-03-01 07:00:00 11 10.4 64.0 2.5 2022-03-01 07:00:00 12 12.3 103.0 4.3 2022-03-01 07:00:00 13 11.2 155.0 3.3 2022-03-01 07:00:00 14 11.5 82.0 3.1 2022-03-01 07:00:00 15 9.1 278.0 2.2 2022-03-01 08:00:00 11 13.2 346.0 3.7 2022-03-01 08:00:00 12 15.0 276.0 4.5 2022-03-01 08:00:00 13 14.4 134.0 2.3 2022-03-01 08:00:00 14 11.9 283.0 3.6 2022-03-01 08:00:00 15 13.5 242.0 3.9 2022-03-01 09:00:00 11 10.0 322.0 2.4 2022-03-01 09:00:00 12 10.0 343.0 2.0 2022-03-01 09:00:00 13 13.3 359.0 3.8 2022-03-01 09:00:00 14 12.1 216.0 4.3 2022-03-01 09:00:00 15 9.2 162.0 2.2 2022-03-01 10:00:00 11 12.0 244.0 3.5 2022-03-01 10:00:00 12 12.8 61.0 4.4 2022-03-01 10:00:00 13 11.2 115.0 3.9 2022-03-01 10:00:00 14 14.6 110.0 3.2 2022-03-01 10:00:00 15 12.0 159.0 2.4 2022-03-01 11:00:00 11 14.4 313.0 4.1 2022-03-01 11:00:00 12 11.1 61.0 4.2 2022-03-01 11:00:00 13 14.1 172.0 4.3 2022-03-01 11:00:00 14 10.1 308.0 3.1 2022-03-01 11:00:00 15 12.9 339.0 2.5 2022-03-01 12:00:00 11 13.1 77.0 3.2 2022-03-01 12:00:00 12 13.9 178.0 1.6 2022-03-01 12:00:00 13 13.2 351.0 3.2 2022-03-01 12:00:00 14 14.9 173.0 3.9 2022-03-01 12:00:00 15 13.6 125.0 4.2 2022-03-01 13:00:00 11 9.7 231.0 2.1 2022-03-01 13:00:00 12 13.1 254.0 2.7 2022-03-01 13:00:00 13 13.0 346.0 2.0 2022-03-01 13:00:00 14 13.2 217.0 4.3 2022-03-01 13:00:00 15 9.4 91.0 2.0 2022-03-01 14:00:00 11 11.3 137.0 1.6 2022-03-01 14:00:00 12 14.2 47.0 4.4 2022-03-01 14:00:00 13 9.8 358.0 3.2 2022-03-01 14:00:00 14 9.6 315.0 4.0 2022-03-01 14:00:00 15 9.6 297.0 3.8 2022-03-01 15:00:00 11 14.7 62.0 1.7 2022-03-01 15:00:00 12 14.5 71.0 2.0 2022-03-01 15:00:00 13 11.5 226.0 3.6 2022-03-01 15:00:00 14 12.9 147.0 2.9 2022-03-01 15:00:00 15 11.3 310.0 3.5 2022-03-01 16:00:00 11 9.3 24.0 1.9 2022-03-01 16:00:00 12 12.8 233.0 3.0 2022-03-01 16:00:00 13 11.3 25.0 1.8 2022-03-01 16:00:00 14 12.5 236.0 1.6 2022-03-01 16:00:00 15 13.5 253.0 4.3 2022-03-01 17:00:00 11 14.1 67.0 1.7 2022-03-01 17:00:00 12 13.3 175.0 4.0 2022-03-01 17:00:00 13 12.6 31.0 3.5 2022-03-01 17:00:00 14 13.7 316.0 3.0 2022-03-01 17:00:00 15 11.8 106.0 3.1 2022-03-01 18:00:00 11 13.6 310.0 3.1 2022-03-01 18:00:00 12 12.3 107.0 4.4 2022-03-01 18:00:00 13 13.7 271.0 2.0 2022-03-01 18:00:00 14 9.6 273.0 2.5 2022-03-01 18:00:00 15 13.9 34.0 3.6 2022-03-01 19:00:00 11 13.3 268.0 1.5 2022-03-01 19:00:00 12 11.9 358.0 1.9 2022-03-01 19:00:00 13 9.3 138.0 2.3 2022-03-01 19:00:00 14 13.7 266.0 3.5 2022-03-01 19:00:00 15 10.3 237.0 4.2 2022-03-01 20:00:00 11 13.9 238.0 4.4 2022-03-01 20:00:00 12 9.5 87.0 3.9 2022-03-01 20:00:00 13 10.9 312.0 2.1 2022-03-01 20:00:00 14 12.3 250.0 4.5 2022-03-01 20:00:00 15 14.1 167

Silver layer - Processing

In [0]:
#Step 3: Silver 

bronze_df = bronze_df.dropDuplicates()

# Calculate average values within each turbine_id group
turbine_window = Window.partitionBy("turbine_id")
filled_df = (
    bronze_df
    .withColumn(
        "wind_speed",
        F.when(F.col("wind_speed").isNull(), F.avg("wind_speed").over(turbine_window)).otherwise(F.col("wind_speed"))
    )
    .withColumn(
        "wind_direction",
        F.when(F.col("wind_direction").isNull(), F.avg("wind_direction").over(turbine_window)).otherwise(F.col("wind_direction"))
    )
    .withColumn(
        "power_output",
        F.when(F.col("power_output").isNull(), F.avg("power_output").over(turbine_window)).otherwise(F.col("power_output"))
    )
)

### ANOMALY REMOVAL ### 

# Define the columns to process
stats_columns = ["wind_speed", "wind_direction", "power_output"]

# Initialize cleaned DataFrame with the original filled DataFrame
cleaned_df = filled_df

for column in stats_columns:
    # Calculate Q1, Q3, and IQR for the column
    q1, q3 = filled_df.approxQuantile(column, [0.25, 0.75], 0)
    iqr = q3 - q1
    lower_bound = q1 - 1.5 * iqr
    upper_bound = q3 + 1.5 * iqr

    # Filter rows based on the IQR bounds
    silver_df = cleaned_df.filter((col(column) >= lower_bound) & (col(column) <= upper_bound))

# Save Silver Layer
silver_df.write.format("delta").mode("overwrite").partitionBy("turbine_id").saveAsTable("silver_turbine_data")
silver_df.display()

timestamp turbine_id wind_speed wind_direction power_output 2022-03-07 04:00:00 1 9.7 44.0 2.7 2022-03-23 19:00:00 1 12.0 87.0 1.7 2022-03-24 15:00:00 1 14.8 311.0 3.8 2022-03-30 01:00:00 1 13.4 321.0 2.9 2022-03-15 00:00:00 1 13.1 216.0 2.6 2022-03-19 03:00:00 1 13.8 10.0 2.6 2022-03-30 14:00:00 1 10.5 195.0 2.1 2022-03-05 18:00:00 1 12.6 162.0 4.2 2022-03-28 12:00:00 1 12.2 223.0 2.4 2022-03-04 20:00:00 1 9.4 126.0 3.4 2022-03-05 19:00:00 1 14.8 328.0 3.5 2022-03-19 04:00:00 1 14.7 171.0 4.0 2022-03-20 21:00:00 1 9.5 144.0 2.7 2022-03-22 17:00:00 1 12.8 220.0 3.8 2022-03-14 16:00:00 1 14.7 181.0 4.3 2022-03-22 11:00:00 1 11.8 173.0 4.0 2022-03-30 08:00:00 1 11.2 5.0 4.4 2022-03-03 07:00:00 1 10.5 225.0 2.6 2022-03-27 05:00:00 1 12.7 334.0 4.0 2022-03-31 05:00:00 1 13.0 232.0 2.1 2022-03-06 20:00:00 1 9.0 342.0 2.1 2022-03-05 01:00:00 1 13.7 24.0 4.3 2022-03-08 10:00:00 1 12.6 163.0 3.7 2022-03-29 21:00:00 1 13.2 205.0 3.2 2022-03-11 04:00:00 1 14.0 241.0 2.8 2022-03-26 21:00:00 1 12.8 68.0 2.9 2022-03-11 13:00:00 1 10.4 59.0 2.5 2022-03-24 23:00:00 1 9.9 243.0 2.1 2022-03-29 11:00:00 1 9.5 200.0 3.0 2022-03-01 18:00:00 1 10.1 240.0 1.8 2022-03-02 18:00:00 1 12.8 50.0 4.0 2022-03-17 06:00:00 1 12.9 150.0 4.1 2022-03-09 02:00:00 1 9.9 10.0 2.1 2022-03-22 22:00:00 1 9.7 56.0 2.4 2022-03-01 14:00:00 1 9.4 316.0 3.9 2022-03-12 10:00:00 1 10.1 55.0 2.0 2022-03-15 06:00:00 1 11.5 173.0 2.4 2022-03-15 21:00:00 1 10.3 274.0 3.4 2022-03-17 04:00:00 1 10.7 198.0 2.2 2022-03-11 02:00:00 1 13.5 35.0 2.4 2022-03-24 12:00:00 1 13.9 16.0 3.5 2022-03-31 19:00:00 1 9.4 75.0 1.9 2022-03-30 21:00:00 1 14.5 202.0 2.3 2022-03-09 20:00:00 1 11.3 170.0 2.0 2022-03-10 15:00:00 1 14.8 227.0 4.3 2022-03-16 13:00:00 1 14.7 78.0 3.4 2022-03-22 15:00:00 1 9.7 335.0 2.3 2022-03-23 01:00:00 1 10.9 123.0 3.8 2022-03-03 11:00:00 1 12.4 246.0 2.1 2022-03-21 17:00:00 1 12.5 119.0 2.5 2022-03-15 18:00:00 1 14.6 50.0 3.7 2022-03-26 01:00:00 1 12.5 222.0 3.3 2022-03-01 22:00:00 1 13.1 286.0 2.2 2022-03-09 15:00:00 1 14.4 307.0 1.6 2022-03-10 23:00:00 1 13.9 22.0 2.6 2022-03-17 23:00:00 1 10.1 292.0 3.3 2022-03-02 00:00:00 1 10.7 101.0 3.4 2022-03-04 04:00:00 1 13.8 38.0 4.2 2022-03-13 15:00:00 1 14.3 157.0 3.3 2022-03-16 05:00:00 1 9.8 39.0 3.7 2022-03-19 09:00:00 1 11.0 33.0 3.4 2022-03-08 01:00:00 1 14.1 153.0 2.1 2022-03-03 13:00:00 1 11.8 251.0 4.0 2022-03-10 19:00:00 1 10.3 285.0 3.8 2022-03-17 08:00:00 1 14.9 138.0 2.3 2022-03-08 09:00:00 1 12.6 267.0 4.5 2022-03-09 09:00:00 1 10.5 173.0 4.1 2022-03-14 13:00:00 1 12.4 275.0 3.2 2022-03-17 20:00:00 1 12.1 57.0 4.4 2022-03-19 11:00:00 1 11.4 356.0 1.9 2022-03-21 07:00:00 1 13.8 112.0 1.7 2022-03-03 05:00:00 1 13.9 94.0 3.7 2022-03-07 14:00:00 1 9.2 31.0 3.0 2022-03-09 03:00:00 1 12.4 51.0 1.6 2022-03-13 13:00:00 1 11.5 151.0 2.2 2022-03-18 17:00:00 1 11.6 63.0 2.5 2022-03-23 03:00:00 1 13.5 199.0 1.7 2022-03-07 19:00:00 1 11.6 338.0 3.8 2022-03-08 07:00:00 1 14.7 225.0 2.7 2022-03-10 02:00:00 1 13.8 82.0 3.0 2022-03-18 12:00:00 1 9.1 70.0 3.7 2022-03-18 14:00:00 1 13.9 91.0 2.1 2022-03-31 03:00:00 1 11.3 214.0 3.3 2022-03-14 23:00:00 1 10.1 88.0 2.9 2022-03-29 18:00:00 1 9.1 263.0 4.5 2022-03-30 04:00:00 1 11.8 111.0 4.3 2022-03-30 18:00:00 1 13.2 278.0 3.1 2022-03-22 23:00:00 1 13.1 319.0 1.7 2022-03-25 20:00:00 1 13.5 147.0 2.2 2022-03-29 15:00:00 1 11.8 299.0 3.5 2022-03-02 08:00:00 1 9.6 129.0 4.1 2022-03-15 11:00:00 1 13.4 156.0 3.9 2022-03-27 11:00:00 1 11.4 6.0 2.3 2022-03-06 16:00:00 1 10.4 263.0 3.8 2022-03-11 11:00:00 1 10.0 22.0 2.0 2022-03-16 10:00:00 1 14.3 309.0 4.4 2022-03-27 08:00:00 1 12.7 81.0 3.7 2022-03-31 02:00:00 1 15.0 295.0 4.0 2022-03-31 15:00:00 1 12.7 261.0 2.5 2022-03-15 14:00:00 1 14.0 185.0 4.1 2022-03-16 21:00:00 1 13.1 198.0 3.4 2022-03-28 00:00:00 1 12.2 201.0 1.7 2022-03-21 04:00:00 1 10.7 348.0 3.8 2022-03-21 09:00:00 1 13.4 221.0 3.7 2022-03-21 12:00:00 1 9.6 305.0 3.6 2022-03-27 04:00:00 1 13.4 187.0 4.0 2022-03-06 07:00:00 1 10.3 307.0 2.3 2022-03-14 12:00:00 1 12.2 1.0 4

Gold layer - Processing & Warehousing 

In [0]:

# Step 3: Gold Layer (Star Schema)

# Create a fact table
silver_df_with_keys = silver_df \
    .withColumn("record_sid", monotonically_increasing_id()) \
    .withColumn("date_key", date_format(to_date("timestamp"), "yyyyMMdd"))

fact_turbine_metrics = silver_df_with_keys.select(
    "record_sid",         
    "turbine_id",    
    "wind_speed",         
    "wind_direction",    
    "power_output",
    "timestamp",
    "date_key"                
)

# Dimension: Time
dim_time_df = cleaned_df.select(to_date("timestamp").alias("date")).distinct() \
    .withColumn("date_key", date_format("date", "yyyyMMdd")) \
    .withColumn("year", year("date")) \
    .withColumn("month", month("date")) \
    .withColumn("day", dayofmonth("date")) \
    .withColumn("day_of_week", dayofweek("date")) \
    .withColumn("quarter", quarter("date")) \
    .select(
        "date_key", "date", "year", "month", "day", "day_of_week", "quarter"
    )

# Dimension: Turbine
dim_turbine_df = (
    cleaned_df.select("turbine_id")
    .distinct()
    .withColumn("location", lit("unknown"))      # Replace "unknown" with actual defaults if available
    .withColumn("manufacturer", lit("unknown")) # Replace "unknown" with actual defaults if available
    .withColumn("capacity", lit("unknown"))     # Replace "unknown" with actual defaults if available
)

# Save the fact and dimension tables
fact_turbine_metrics.write.format("delta").mode("overwrite").saveAsTable("gold_fact_turbine_metrics")
dim_time_df.write.format("delta").mode("overwrite").saveAsTable("gold_dim_time")
dim_turbine_df.write.format("delta").mode("overwrite").saveAsTable("gold_dim_turbine")

fact_turbine_metrics.display()

record_sid turbine_id wind_speed wind_direction power_output timestamp date_key 0 1 9.7 44.0 2.7 2022-03-07 04:00:00 20220307 1 1 12.0 87.0 1.7 2022-03-23 19:00:00 20220323 2 1 14.8 311.0 3.8 2022-03-24 15:00:00 20220324 3 1 13.4 321.0 2.9 2022-03-30 01:00:00 20220330 4 1 13.1 216.0 2.6 2022-03-15 00:00:00 20220315 5 1 13.8 10.0 2.6 2022-03-19 03:00:00 20220319 6 1 10.5 195.0 2.1 2022-03-30 14:00:00 20220330 7 1 12.6 162.0 4.2 2022-03-05 18:00:00 20220305 8 1 12.2 223.0 2.4 2022-03-28 12:00:00 20220328 9 1 9.4 126.0 3.4 2022-03-04 20:00:00 20220304 10 1 14.8 328.0 3.5 2022-03-05 19:00:00 20220305 11 1 14.7 171.0 4.0 2022-03-19 04:00:00 20220319 12 1 9.5 144.0 2.7 2022-03-20 21:00:00 20220320 13 1 12.8 220.0 3.8 2022-03-22 17:00:00 20220322 14 1 14.7 181.0 4.3 2022-03-14 16:00:00 20220314 15 1 11.8 173.0 4.0 2022-03-22 11:00:00 20220322 16 1 11.2 5.0 4.4 2022-03-30 08:00:00 20220330 17 1 10.5 225.0 2.6 2022-03-03 07:00:00 20220303 18 1 12.7 334.0 4.0 2022-03-27 05:00:00 20220327 19 1 13.0 232.0 2.1 2022-03-31 05:00:00 20220331 20 1 9.0 342.0 2.1 2022-03-06 20:00:00 20220306 21 1 13.7 24.0 4.3 2022-03-05 01:00:00 20220305 22 1 12.6 163.0 3.7 2022-03-08 10:00:00 20220308 23 1 13.2 205.0 3.2 2022-03-29 21:00:00 20220329 24 1 14.0 241.0 2.8 2022-03-11 04:00:00 20220311 25 1 12.8 68.0 2.9 2022-03-26 21:00:00 20220326 26 1 10.4 59.0 2.5 2022-03-11 13:00:00 20220311 27 1 9.9 243.0 2.1 2022-03-24 23:00:00 20220324 28 1 9.5 200.0 3.0 2022-03-29 11:00:00 20220329 29 1 10.1 240.0 1.8 2022-03-01 18:00:00 20220301 30 1 12.8 50.0 4.0 2022-03-02 18:00:00 20220302 31 1 12.9 150.0 4.1 2022-03-17 06:00:00 20220317 32 1 9.9 10.0 2.1 2022-03-09 02:00:00 20220309 33 1 9.7 56.0 2.4 2022-03-22 22:00:00 20220322 34 1 9.4 316.0 3.9 2022-03-01 14:00:00 20220301 35 1 10.1 55.0 2.0 2022-03-12 10:00:00 20220312 36 1 11.5 173.0 2.4 2022-03-15 06:00:00 20220315 37 1 10.3 274.0 3.4 2022-03-15 21:00:00 20220315 38 1 10.7 198.0 2.2 2022-03-17 04:00:00 20220317 39 1 13.5 35.0 2.4 2022-03-11 02:00:00 20220311 40 1 13.9 16.0 3.5 2022-03-24 12:00:00 20220324 41 1 9.4 75.0 1.9 2022-03-31 19:00:00 20220331 42 1 14.5 202.0 2.3 2022-03-30 21:00:00 20220330 43 1 11.3 170.0 2.0 2022-03-09 20:00:00 20220309 44 1 14.8 227.0 4.3 2022-03-10 15:00:00 20220310 45 1 14.7 78.0 3.4 2022-03-16 13:00:00 20220316 46 1 9.7 335.0 2.3 2022-03-22 15:00:00 20220322 47 1 10.9 123.0 3.8 2022-03-23 01:00:00 20220323 48 1 12.4 246.0 2.1 2022-03-03 11:00:00 20220303 49 1 12.5 119.0 2.5 2022-03-21 17:00:00 20220321 50 1 14.6 50.0 3.7 2022-03-15 18:00:00 20220315 51 1 12.5 222.0 3.3 2022-03-26 01:00:00 20220326 52 1 13.1 286.0 2.2 2022-03-01 22:00:00 20220301 53 1 14.4 307.0 1.6 2022-03-09 15:00:00 20220309 54 1 13.9 22.0 2.6 2022-03-10 23:00:00 20220310 55 1 10.1 292.0 3.3 2022-03-17 23:00:00 20220317 56 1 10.7 101.0 3.4 2022-03-02 00:00:00 20220302 57 1 13.8 38.0 4.2 2022-03-04 04:00:00 20220304 58 1 14.3 157.0 3.3 2022-03-13 15:00:00 20220313 59 1 9.8 39.0 3.7 2022-03-16 05:00:00 20220316 60 1 11.0 33.0 3.4 2022-03-19 09:00:00 20220319 61 1 14.1 153.0 2.1 2022-03-08 01:00:00 20220308 62 1 11.8 251.0 4.0 2022-03-03 13:00:00 20220303 63 1 10.3 285.0 3.8 2022-03-10 19:00:00 20220310 64 1 14.9 138.0 2.3 2022-03-17 08:00:00 20220317 65 1 12.6 267.0 4.5 2022-03-08 09:00:00 20220308 66 1 10.5 173.0 4.1 2022-03-09 09:00:00 20220309 67 1 12.4 275.0 3.2 2022-03-14 13:00:00 20220314 68 1 12.1 57.0 4.4 2022-03-17 20:00:00 20220317 69 1 11.4 356.0 1.9 2022-03-19 11:00:00 20220319 70 1 13.8 112.0 1.7 2022-03-21 07:00:00 20220321 71 1 13.9 94.0 3.7 2022-03-03 05:00:00 20220303 72 1 9.2 31.0 3.0 2022-03-07 14:00:00 20220307 73 1 12.4 51.0 1.6 2022-03-09 03:00:00 20220309 74 1 11.5 151.0 2.2 2022-03-13 13:00:00 20220313 75 1 11.6 63.0 2.5 2022-03-18 17:00:00 20220318 76 1 13.5 199.0 1.7 2022-03-23 03:00:00 20220323 77 1 11.6 338.0 3.8 2022-03-07 19:00:00 20220307 78 1 14.7 225.0 2.7 2022-03-08 07:00:00 20220308 79 1 13.8 82.0 3.0 2022-03-10 02:00:00 20220310 80 1 9.1 70.0 3.7 2022-03-18 12:00:00 20220318 81 

Summary statistics

In [0]:
# Define the time period (e.g., extract the date for grouping by 24 hours)
daily_summary_df = fact_turbine_metrics \
    .groupBy("turbine_id", "date_key") \
    .agg(
        min("power_output").alias("min_power_output"),
        max("power_output").alias("max_power_output"),
        avg("power_output").alias("avg_power_output")
    )
    
daily_summary_df.write.format("delta").mode("overwrite").saveAsTable("gold_daily_summary")
daily_summary_df.display()

turbine_id date_key min_power_output max_power_output avg_power_output 1 20220307 1.9 4.3 3.283333333333333 1 20220323 1.7 4.4 3.2249999999999996 1 20220324 1.6 4.3 2.9791666666666665 1 20220330 1.5 4.4 3.0500000000000003 1 20220315 1.6 4.4 3.0124999999999997 1 20220319 1.8 4.5 3.1250000000000004 1 20220305 1.6 4.3 3.2458333333333322 1 20220328 1.6 4.5 3.0749999999999993 1 20220304 1.5 4.4 2.9874999999999994 1 20220320 1.6 3.8 2.716666666666667 1 20220322 1.6 4.2 2.8125000000000004 1 20220314 1.6 4.3 3.025 1 20220303 1.6 4.4 2.9250000000000003 1 20220327 1.7 4.4 3.1 1 20220331 1.6 4.3 2.958333333333334 1 20220306 1.5 4.4 2.958333333333334 1 20220308 1.7 4.5 3.291666666666666 1 20220329 1.5 4.5 3.1291666666666664 1 20220311 1.5 4.4 2.5750000000000006 1 20220326 1.5 4.5 2.816666666666667 1 20220301 1.6 4.4 2.975 1 20220302 1.9 4.5 3.2374999999999994 1 20220317 1.6 4.4 3.0208333333333335 1 20220309 1.5 4.5 2.8375000000000004 1 20220312 1.6 4.2 2.820833333333333 1 20220310 1.7 4.3 3.120833333333334 1 20220316 1.6 4.4 2.979166666666666 1 20220321 1.7 4.4 3.149999999999999 1 20220313 1.5 4.5 2.9041666666666672 1 20220318 1.6 4.5 3.1041666666666665 1 20220325 1.5 4.4 3.066666666666667 2 20220314 1.5 4.1 3.0166666666666675 2 20220324 1.6 4.4 3.1583333333333328 2 20220301 1.6 4.4 2.9833333333333325 2 20220303 1.5 4.5 3.158333333333333 2 20220313 2.0 4.3 3.0375 2 20220323 1.5 4.3 2.9666666666666663 2 20220330 1.7 4.4 3.049999999999999 2 20220319 1.5 4.4 2.7875 2 20220321 1.7 4.4 3.1583333333333337 2 20220309 1.5 4.4 2.9625 2 20220329 1.5 4.3 3.0416666666666665 2 20220306 1.7 4.3 3.1375000000000006 2 20220312 1.6 4.5 3.0208333333333326 2 20220331 1.6 4.4 3.2291666666666674 2 20220322 1.6 4.5 2.920833333333334 2 20220308 1.6 4.4 3.079166666666666 2 20220304 1.7 4.4 3.0083333333333333 2 20220307 1.7 4.4 3.0 2 20220318 1.5 4.3 2.7375000000000003 2 20220325 1.6 4.3 2.7249999999999996 2 20220317 1.5 4.5 2.875 2 20220316 1.9 4.3 3.0625 2 20220328 1.6 4.5 2.858333333333333 2 20220315 1.5 4.5 3.1125000000000003 2 20220311 1.6 4.4 3.0750000000000006 2 20220320 1.7 4.5 2.7125000000000004 2 20220310 1.6 4.5 2.816666666666666 2 20220302 1.6 4.2 2.4666666666666663 2 20220327 1.5 4.4 3.2416666666666667 2 20220326 1.5 4.5 2.9875000000000003 2 20220305 1.6 4.5 3.1041666666666674 3 20220320 1.7 4.5 2.958333333333334 3 20220312 1.6 4.3 3.070833333333334 3 20220318 1.5 4.5 2.8958333333333335 3 20220301 1.6 4.5 2.766666666666666 3 20220309 1.5 4.4 3.0 3 20220310 1.7 4.5 3.1875 3 20220313 1.6 4.4 2.9791666666666665 3 20220317 1.5 4.4 3.2499999999999996 3 20220321 1.5 4.4 3.3416666666666663 3 20220324 1.9 4.4 3.1583333333333337 3 20220325 1.8 4.5 3.0374999999999996 3 20220330 1.6 4.5 2.7875 3 20220304 1.6 4.2 2.879166666666667 3 20220322 1.6 4.5 2.983333333333334 3 20220326 1.6 4.4 2.733333333333333 3 20220302 1.6 4.4 2.9791666666666665 3 20220307 1.5 4.3 2.808333333333333 3 20220303 1.8 4.4 3.2541666666666664 3 20220314 1.6 3.9 2.8083333333333336 3 20220308 1.7 4.4 3.383333333333333 3 20220319 1.8 4.5 3.1291666666666664 3 20220329 1.7 4.4 2.904166666666667 3 20220306 1.7 4.4 3.3000000000000003 3 20220327 1.6 4.4 2.8375000000000004 3 20220331 1.5 4.3 2.879166666666667 3 20220328 1.6 4.2 2.6875 3 20220316 1.8 4.3 2.9041666666666663 3 20220311 1.6 4.4 3.025 3 20220323 1.5 4.2 2.795833333333333 3 20220315 1.7 4.5 3.0333333333333337 3 20220305 1.6 4.5 2.6208333333333327 4 20220325 1.7 4.3 3.2708333333333335 4 20220310 1.9 4.4 3.1875 4 20220321 1.6 4.5 2.9499999999999997 4 20220326 1.5 4.4 2.470833333333333 4 20220330 1.6 4.4 3.108333333333334 4 20220302 1.5 4.2 3.108333333333334 4 20220329 1.6 4.2 2.8249999999999997 4 20220308 1.5 4.5 2.8541666666666665 4 20220303 1.8 4.3 3.0500000000000003 4 20220307 1.5 4.4 2.9791666666666665 4 20220311 1.5 4.3 2.4791666666666665 4 20220304 1.5 4.5 2.9499999999999997 4 20220319 1.5 4.4 2.7583333333333333 4 20220316 1.6 4.4 2.8708333333333336 4 20220320 1.6 4.2 2.504166666666667 4 20220323 1.8 4.5 3.316666666666666 4 20220305 1.

In [0]:

# Step 1: Calculate mean and standard deviation for each turbine over a given period (e.g., daily)
stats_df = fact_turbine_metrics \
    .groupBy("turbine_id", "date_key") \
    .agg(
        mean("power_output").alias("mean_power_output"),
        stddev("power_output").alias("stddev_power_output")
    )

# Step 2: Join the calculated statistics back to the fact table
joined_df = fact_turbine_metrics.join(stats_df, on=["turbine_id", "date_key"], how="inner")

# Step 3: Identify anomalies (output outside ±2 standard deviations from the mean)
anomalies_df = joined_df.filter(
    (col("power_output") > col("mean_power_output") + 2 * col("stddev_power_output")) |
    (col("power_output") < col("mean_power_output") - 2 * col("stddev_power_output"))
).select("turbine_id", "date_key", "power_output", "mean_power_output", "stddev_power_output")

# Show the anomalies
anomalies_df.display()
anomalies_df.write.format("delta").mode("overwrite").saveAsTable("gold_anomalies")


turbine_id date_key power_output mean_power_output stddev_power_output 1 20220305 1.6 3.2458333333333322 0.7150428182172436 1 20220329 1.5 3.1291666666666664 0.8110536178419356 1 20220311 4.4 2.5750000000000006 0.779771426932835 1 20220326 4.5 2.816666666666667 0.8354465958352776 2 20220331 1.6 3.2291666666666674 0.7123013325874079 2 20220322 4.5 2.920833333333334 0.7835144718103375 2 20220328 4.5 2.858333333333333 0.8139632865701364 2 20220302 4.2 2.4666666666666663 0.7545033878776428 3 20220317 1.5 3.2499999999999996 0.8387361091961912 3 20220321 1.5 3.3416666666666663 0.8581662282811638 3 20220303 1.9 3.2541666666666664 0.6691845567662875 3 20220303 1.8 3.2541666666666664 0.6691845567662875 3 20220305 4.5 2.6208333333333327 0.8214404986081603 4 20220325 1.7 3.2708333333333335 0.7664027586105083 4 20220326 4.4 2.470833333333333 0.8400202723571704 4 20220311 4.3 2.4791666666666665 0.7300858595527244 4 20220320 4.1 2.504166666666667 0.75841893130533 4 20220320 4.2 2.504166666666667 0.75841893130533 4 20220305 4.5 2.8375000000000004 0.7394548520774408 4 20220305 4.4 2.8375000000000004 0.7394548520774408 4 20220309 4.4 2.866666666666667 0.7263168949460409 6 20220310 4.4 2.6791666666666667 0.8402790254312612 6 20220314 1.7 3.2416666666666667 0.7131782304626224 6 20220320 4.4 2.7000000000000006 0.8288284030721501 7 20220313 4.5 2.724999999999999 0.8724029782856882 7 20220305 4.5 2.704166666666666 0.8834119461874321 7 20220329 1.5 3.0083333333333333 0.721060008759246 8 20220317 4.3 2.720833333333333 0.6672325496873776 8 20220304 4.0 2.529166666666667 0.6962503089791939 8 20220304 4.1 2.529166666666667 0.6962503089791939 9 20220331 1.6 3.274999999999999 0.7484767139359432 9 20220316 1.7 2.9791666666666665 0.6171316304285192 9 20220315 1.8 3.470833333333333 0.8243464693011521 9 20220315 1.7 3.470833333333333 0.8243464693011521 9 20220329 4.1 2.5749999999999997 0.7490573786578295 10 20220310 4.5 3.0374999999999996 0.7137241581402743 10 20220310 1.5 3.0374999999999996 0.7137241581402743 10 20220331 4.3 2.704166666666667 0.768668621237632 10 20220313 4.4 2.8458333333333337 0.7740234614277397 10 20220329 1.6 3.216666666666667 0.7855580495898201 10 20220306 4.5 2.766666666666667 0.8463048410933091 11 20220305 4.4 2.8375000000000004 0.7705517503711222 11 20220319 4.2 2.7916666666666665 0.6990158713547191 11 20220308 4.3 2.579166666666667 0.780177887556347 11 20220308 4.2 2.579166666666667 0.780177887556347 11 20220322 4.5 2.5541666666666667 0.8807008901840706 12 20220303 4.2 2.670833333333333 0.7357215722568273 12 20220305 1.6 3.283333333333333 0.7393691004272945 12 20220319 1.6 3.3874999999999997 0.8289923165322857 13 20220314 1.7 3.329166666666667 0.7601368107219205 13 20220314 1.6 3.329166666666667 0.7601368107219205 14 20220327 1.6 2.966666666666667 0.6098229726494521 14 20220331 1.6 3.304166666666666 0.8492857186389382 14 20220331 1.6 3.304166666666666 0.8492857186389382 14 20220314 4.5 2.7249999999999996 0.8598533747604625 14 20220322 4.5 2.8416666666666663 0.7412777843853061 15 20220322 4.5 2.995833333333333 0.7285955320171558 15 20220319 4.3 2.7125 0.7176728696461132

Machine learning

In [0]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression

# Prepare the data
features = ["wind_speed", "wind_direction"]
assembler = VectorAssembler(inputCols=features, outputCol="features")
data = assembler.transform(fact_turbine_metrics).select("features", "power_output")

# Split into training and test sets
train_data, test_data = data.randomSplit([0.8, 0.2], seed=42)

# Train a Linear Regression model
lr = LinearRegression(featuresCol="features", labelCol="power_output")
lr_model = lr.fit(train_data)

# Evaluate the model
predictions = lr_model.transform(test_data)
predictions.select("features", "power_output", "prediction").display()


features power_output prediction Map(vectorType -> dense, length -> 2, values -> List(9.0, 12.0)) 3.4 2.9960878042254326 Map(vectorType -> dense, length -> 2, values -> List(9.0, 26.0)) 1.8 2.9970752271879713 Map(vectorType -> dense, length -> 2, values -> List(9.0, 31.0)) 2.8 2.997427878246021 Map(vectorType -> dense, length -> 2, values -> List(9.0, 50.0)) 1.9 2.998767952266609 Map(vectorType -> dense, length -> 2, values -> List(9.0, 67.0)) 3.3 2.999966965863978 Map(vectorType -> dense, length -> 2, values -> List(9.0, 92.0)) 3.1 3.0017302211542254 Map(vectorType -> dense, length -> 2, values -> List(9.0, 114.0)) 4.5 3.0032818858096437 Map(vectorType -> dense, length -> 2, values -> List(9.0, 144.0)) 3.0 3.0053977921579413 Map(vectorType -> dense, length -> 2, values -> List(9.0, 194.0)) 2.3 3.008924302738437 Map(vectorType -> dense, length -> 2, values -> List(9.0, 201.0)) 3.3 3.0094180142197064 Map(vectorType -> dense, length -> 2, values -> List(9.0, 211.0)) 1.9 3.010123316335805 Map(vectorType -> dense, length -> 2, values -> List(9.0, 224.0)) 2.7 3.011040209086734 Map(vectorType -> dense, length -> 2, values -> List(9.0, 226.0)) 1.5 3.011181269509954 Map(vectorType -> dense, length -> 2, values -> List(9.0, 239.0)) 3.8 3.012098162260883 Map(vectorType -> dense, length -> 2, values -> List(9.0, 260.0)) 2.5 3.013579296704691 Map(vectorType -> dense, length -> 2, values -> List(9.0, 286.0)) 1.6 3.015413082206549 Map(vectorType -> dense, length -> 2, values -> List(9.0, 312.0)) 4.0 3.0172468677084066 Map(vectorType -> dense, length -> 2, values -> List(9.1, 12.0)) 2.0 2.995821894831991 Map(vectorType -> dense, length -> 2, values -> List(9.1, 31.0)) 2.7 2.9971619688525792 Map(vectorType -> dense, length -> 2, values -> List(9.1, 45.0)) 1.7 2.9981493918151183 Map(vectorType -> dense, length -> 2, values -> List(9.1, 48.0)) 3.0 2.998360982449948 Map(vectorType -> dense, length -> 2, values -> List(9.1, 48.0)) 3.7 2.998360982449948 Map(vectorType -> dense, length -> 2, values -> List(9.1, 71.0)) 4.2 2.999983177316976 Map(vectorType -> dense, length -> 2, values -> List(9.1, 85.0)) 2.5 3.0009706002795147 Map(vectorType -> dense, length -> 2, values -> List(9.1, 108.0)) 4.3 3.0025927951465428 Map(vectorType -> dense, length -> 2, values -> List(9.1, 144.0)) 2.7 3.0051318827644997 Map(vectorType -> dense, length -> 2, values -> List(9.1, 148.0)) 3.4 3.0054140036109396 Map(vectorType -> dense, length -> 2, values -> List(9.1, 151.0)) 3.3 3.0056255942457692 Map(vectorType -> dense, length -> 2, values -> List(9.1, 157.0)) 1.5 3.0060487755154286 Map(vectorType -> dense, length -> 2, values -> List(9.1, 174.0)) 4.4 3.0072477891127973 Map(vectorType -> dense, length -> 2, values -> List(9.1, 188.0)) 3.5 3.008235212075336 Map(vectorType -> dense, length -> 2, values -> List(9.1, 219.0)) 3.8 3.0104216486352433 Map(vectorType -> dense, length -> 2, values -> List(9.1, 233.0)) 3.9 3.011409071597782 Map(vectorType -> dense, length -> 2, values -> List(9.1, 251.0)) 3.3 3.0126786154067604 Map(vectorType -> dense, length -> 2, values -> List(9.1, 263.0)) 4.5 3.0135249779460795 Map(vectorType -> dense, length -> 2, values -> List(9.1, 286.0)) 4.4 3.0151471728131076 Map(vectorType -> dense, length -> 2, values -> List(9.1, 305.0)) 3.8 3.016487246833696 Map(vectorType -> dense, length -> 2, values -> List(9.1, 315.0)) 2.8 3.017192548949795 Map(vectorType -> dense, length -> 2, values -> List(9.1, 323.0)) 2.7 3.0177567906426743 Map(vectorType -> dense, length -> 2, values -> List(9.1, 324.0)) 3.7 3.0178273208542845 Map(vectorType -> dense, length -> 2, values -> List(9.1, 331.0)) 4.4 3.0183210323355536 Map(vectorType -> dense, length -> 2, values -> List(9.1, 333.0)) 2.1 3.0184620927587735 Map(vectorType -> dense, length -> 2, values -> List(9.1, 359.0)) 3.4 3.0202958782606313 Map(vectorType -> dense, length -> 2, values -> List(9.2, 13.0)) 2.6 2.9956265156501596 Map(vectorType -> dense, length -> 2, values -> List(9.2, 14.0)) 3.7 2.995697045861

In [0]:
from pyspark.ml.classification import LogisticRegression

# Label data for anomalies (e.g., power_output < threshold)
threshold = 100  # Example threshold
labeled_df = fact_turbine_metrics.withColumn(
    "label", when(col("power_output") < threshold, 1).otherwise(0)
)

# Prepare the data
features = ["wind_speed", "wind_direction"]
assembler = VectorAssembler(inputCols=features, outputCol="features")
data = assembler.transform(labeled_df).select("features", "label")

# Split into training and test sets
train_data, test_data = data.randomSplit([0.8, 0.2], seed=42)

# Train a Logistic Regression model
lr = LogisticRegression(featuresCol="features", labelCol="label")
lr_model = lr.fit(train_data)

# Evaluate the model
predictions = lr_model.transform(test_data)
predictions.select("features", "label", "prediction", "probability").display()
